In [9]:
#-- information on simulations to be processed:
IOP = 'ches_IOP2' # ches_IOP2 or ches_IOP03
EM  = 'ensemble.member.7' # 1-8

# em1: simulations = ['01.ches_IOP2.24050','02.ches_IOP2.10023','03.ches_IOP2.28390','04.ches_IOP2.20941','05.ches_IOP2.13864','06.ches_IOP2.31028','07.ches_IOP2.19931','08.ches_IOP2.19743']
# em2: simulations = ['01.ches_IOP2.20255','02.ches_IOP2.13449','03.ches_IOP2.733','04.ches_IOP2.18198','05.ches_IOP2.19794','06.ches_IOP2.11638','07.ches_IOP02.31113'] # add other simulations of ensemble member (IOP2 ensemble member 2: (1) 20255 (2) 13449 (3) 733 (4) 18198 (5) 19794 (6) 11638 (7) 31113)
# em3: simulations =  ['01.ches_IOP2.2199','02.ches_IOP2.11581','03.ches_IOP2.26923','04.ches_IOP2.16339','05.ches_IOP2.10214','06.ches_IOP2.17190','07.ches_IOP2.19176']
# em4: simulations = ['01.ches_IOP2.5461','02.ches_IOP2.19281','03.ches_IOP2.11295','04.ches_IOP2.14610','05.ches_IOP2.24393','06. ches_IOP2.29130','07. ches_IOP2.18966']
# em5: simulations = ['01.ches_IOP2.27066','02.ches_IOP2.28641','03.ches_IOP2.4709','04.ches_IOP2.26733','05. ches_IOP2.16063','06.ches_IOP2.15821','07.ches_IOP2.28647']
# em6: simulations = ['01.ches_IOP2.15881','02.ches_IOP2.16506','03.ches_IOP2.9028','04.ches_IOP2.797','05.ches_IOP2.23005','06.ches_IOP2.24108','07.ches_IOP2.6117']
simulations = ['01.ches_IOP02.12798','02.ches_IOP02.5527','03.ches_IOP02.16221','04.ches_IOP02.30862','05.ches_IOP02.32477','06.ches_IOP02.17608','07.ches_IOP02.29345']
# em8: simulations = ['1.ches_IOP2.11058','2.ches_IOP2.20781','3.ches_IOP2.1521','04.ches_IOP2.1455','05. ches_IOP2.31525','06.ches_IOP2.1409','07.ches_IOP2.31095']

print(simulations)
#-- IOP2 - ensemble 2:
#-- (1) 20255 (2) 13449 (3) 733 (4) 18198 (5) 19794 (6) 11638 (7) 31113
#-----------------------------------------------------------------------------

import xarray as xr
import numpy as np
import os
import timeit
start_time = timeit.default_timer()
pathI  = '/bog/incoming/CHEESEHEAD/palm/realistic_runs/' #'/glade/scratch/sreenath/palm/current_version/tmp/'+sim+'/OUTPUT/'#'C:/Luise/PALM/idealizedHeterogeneity/simulations/'
pathO = '/air/lwanner/' #'/glade/scratch/lwanner/palm/current_version/tmp/'+sim+'/OUTPUT/subsetLW/'

#-- output files to loop through
fls   = ['ms','pr','pr_c1','ts','ts_c1','xy','xy_c1','3d','3d_c1']  #,'xy_p','3d_p'
#-- filenames of output files
flnm  = {'ms':    'DATA_MASK_NETCDF_N03_M',
         'pr':    'DATA_1D_PR_NETCDF_N03slice',
         'pr_c1': 'DATA_1D_PR_NETCDF_N02slice',
         'ts':    'DATA_1D_TS_NETCDF_N03slice',
         'ts_c1': 'DATA_1D_TS_NETCDF_N02slice',
         'xy':    'DATA_2D_XY_AV_NETCDF_N03slice',
         'xy_c1': 'DATA_2D_XY_AV_NETCDF_N02slice',
         # 'xy_p':  'DATA_2D_XY_AV_NETCDFslice',
         '3d':    'DATA_3D_AV_NETCDF_N03',
         '3d_c1': 'DATA_3D_AV_NETCDF_N02',
         # '3d_p':  'DATA_3D_AV_NETCDF',
         }
#-- variables to extract from each output file
xtrct = {'ms':    ['theta','q'],
         'pr':    ['theta','q','w"theta"','w"q"','w"u"','w"v"'],
         'pr_c1': ['theta','q','w"theta"','w"q"','w"u"','w"v"','rho'],
         'ts':    ['zi_wtheta'],
         'ts_c1': ['zi_wtheta'],
         'xy':    ['shf*_xy','qsws*_xy','tsurf*_xy'],
         'xy_c1': ['tsurf*_xy'],
         # 'xy_p':  ['tsurf*_xy'],
         '3d':    ['u','v','w','theta','q','wtheta','wq','uw','vw'],
         '3d_c1': ['theta','q'],
         # '3d_p':  ['theta'],
         }
#-- list of towers (masked output)
ms_lst = ['02','03','06','07','08','09','10','11','12','13','14','15','17']


['01.ches_IOP02.12798', '02.ches_IOP02.5527', '03.ches_IOP02.16221', '04.ches_IOP02.30862', '05.ches_IOP02.32477', '06.ches_IOP02.17608', '07.ches_IOP02.29345']


In [ ]:
#-- loop through ensemble members
for s in np.arange(len(simulations)):
    pathIN = pathI + IOP + '/' + EM + '/' + simulations[s] + '/'
    pathOUT = pathO + IOP + '/' + EM + '/' + simulations[s] + '/'
    if not os.path.exists(pathOUT):
        os.makedirs(pathOUT)
    #-- loop through output data sets
    for f in range(len(fls)):
        #-- if dataset is masked output, extract y amd x information of tower locations for later
        if fls[f] == 'ms':
            y_lst = []
            yv_lst = []
            x_lst = []
            xu_lst = []
            for i in range(len(ms_lst)):
                print('Reading: '+pathIN+flnm[fls[f]]+ms_lst[i]+'slice')
                if '.1' not in EM:
                    dsIN = xr.open_dataset(pathIN+flnm[fls[f]]+ms_lst[i]+'slice',decode_times=None,engine='netcdf4')
                #-- only for ensemble member 1 where tower output is missing in the first simulation:
                elif '.1' in EM:
                    pINem1 = pathI + IOP + '/' + EM + '/' + simulations[1] + '/'
                    dsIN = xr.open_dataset(pINem1+flnm[fls[f]]+ms_lst[i]+'slice',decode_times=None,engine='netcdf4')

                variables = xtrct[fls[f]]  ## variables to extract
                dsOUT = dsIN[variables]  ## dataset with extracted variables
                
                #-- get x,y,xu,yv values
                masked_y = np.array(dsIN['y'])
                masked_yv = np.array(dsIN['yv'])
                masked_x = np.array(dsIN['x'])
                masked_xu = np.array(dsIN['xu'])
                #-- add 1on each side for child 2 domain and add to list (5x5 pixels at each tower location to calculate dispersive fluxes)
                y_lst.append(np.concatenate((np.array([masked_y.min() -int(masked_y[1] -masked_y[0])]), masked_y, (np.array([masked_y.max() +int(masked_y[1] -masked_y[0]) ])))))
                yv_lst.append(np.concatenate((np.array([masked_yv.min()-int(masked_yv[1]-masked_yv[0])]),masked_yv,(np.array([masked_yv.max()+int(masked_yv[1]-masked_yv[0])])))))
                x_lst.append(np.concatenate((np.array([masked_x.min() -int(masked_x[1] -masked_x[0])]), masked_x, (np.array([masked_x.max() +int(masked_x[1] -masked_x[0]) ])))))
                xu_lst.append(np.concatenate((np.array([masked_xu.min()-int(masked_xu[1]-masked_xu[0])]),masked_xu,(np.array([masked_xu.max()+int(masked_xu[1]-masked_xu[0])])))))
                #-- save dataset with extracted variables
                print('Saving: '+pathOUT+flnm[fls[f]]+ms_lst[i]+'slice_subsetLW')
                print('Storage needed :'+str(dsOUT.nbytes))
                dsOUT.to_netcdf(pathOUT+flnm[fls[f]]+ms_lst[i]+'slice_subsetLW',engine='netcdf4')
                dsIN.close()

        elif fls[f] == '3d':
            print('Reading: '+pathIN+flnm[fls[f]]+'slice')
            dsIN = xr.open_dataset(pathIN+flnm[fls[f]]+'slice',decode_times=None,engine='netcdf4')  ## read file 
            variables = xtrct[fls[f]]  ## variables to extract
            dsOUT = dsIN[variables]  ## dataset with extracted variables
            dsIN.close()
            #-- loop through coordinates for each towert to generate 3d output for each tower location
            for i in range(len(ms_lst)):
                dsOUT_3d2ms = dsOUT.sel(y=y_lst[i],x=x_lst[i],yv=yv_lst[i],xu=xu_lst[i]) #-- select tower location only (xy)
                print('Saving: '+pathOUT+flnm[fls[f]]+'_M'+ms_lst[i]+'slice_subsetLW')
                print('Storage needed :'+str(dsOUT_3d2ms.nbytes))
                dsOUT_3d2ms.to_netcdf(pathOUT+flnm[fls[f]]+'_M'+ms_lst[i]+'slice_subsetLW',engine='netcdf4')
                dsOUT_3d2ms.close()
            dsOUT.close()

        elif '3d_' in fls[f]: #-- 3d_c1 and 3d_p
            print('Reading: '+pathIN+flnm[fls[f]]+'slice')
            dsIN = xr.open_dataset(pathIN+flnm[fls[f]]+'slice',decode_times=None,engine='netcdf4')  ## read file 
            variables = xtrct[fls[f]]  ## variables to extract
            dsOUT = dsIN[variables]  ## dataset with extracted variables
            dsIN.close()
            #-- loop through coordinates for each tower to generate 3d output for each tower location
            for i in range(len(ms_lst)):
                indx = int(len(y_lst[i])/2)
                y_lst_c1 = np.squeeze(dsOUT['y'])[np.where(np.abs(y_lst[i][indx]-np.squeeze(dsOUT['y'])) <= 50)]
                x_lst_c1 = np.squeeze(dsOUT['x'])[np.where(np.abs(x_lst[i][indx]-np.squeeze(dsOUT['x'])) <= 50)]
                #print(x_lst[i][indx], x_lst_c1)
                #print(y_lst[i][indx], np.squeeze(y_lst_c1))
                dsOUT_3d2ms = dsOUT.sel(y=y_lst_c1,x=x_lst_c1) #,yv=yv_lst_c1,xu=xu_lst_c1
                print('Saving: '+pathOUT+flnm[fls[f]]+'_M'+ms_lst[i]+'slice_subsetLW')
                print('Storage needed :'+str(dsOUT_3d2ms.nbytes))
                dsOUT_3d2ms.to_netcdf(pathOUT+flnm[fls[f]]+'_M'+ms_lst[i]+'slice_subsetLW',engine='netcdf4')
                dsOUT_3d2ms.close()
                #raise SystemExit("Stop right there!")
            dsOUT.close()
            
        else: #-- for all output files other than masked output or 3d output
            print('Reading: '+pathIN+flnm[fls[f]])
            dsIN = xr.open_dataset(pathIN+flnm[fls[f]],decode_times=None,engine='netcdf4')  ## read file 
            variables = xtrct[fls[f]]  ## variables to extract
            dsOUT = dsIN[variables]  ## dataset with extracted variables
            dsIN.close()
            print('Saving: '+pathOUT+flnm[fls[f]]+'_subsetLW')
            print('Storage needed :'+str(dsOUT.nbytes))
            dsOUT.to_netcdf(pathOUT+flnm[fls[f]]+'_subsetLW',engine='netcdf4')
            dsOUT.close()
        
elapsed = timeit.default_timer() - start_time
print('Time elapsed:',elapsed, 'seconds')
print('Done!')

Reading: /bog/incoming/CHEESEHEAD/palm/realistic_runs/ches_IOP2/ensemble.member.7/01.ches_IOP02.12798/DATA_MASK_NETCDF_N03_M02slice
Saving: /air/lwanner/ches_IOP2/ensemble.member.7/01.ches_IOP02.12798/DATA_MASK_NETCDF_N03_M02slice_subsetLW
Storage needed :3158248
Reading: /bog/incoming/CHEESEHEAD/palm/realistic_runs/ches_IOP2/ensemble.member.7/01.ches_IOP02.12798/DATA_MASK_NETCDF_N03_M03slice
Saving: /air/lwanner/ches_IOP2/ensemble.member.7/01.ches_IOP02.12798/DATA_MASK_NETCDF_N03_M03slice_subsetLW
Storage needed :5188520
Reading: /bog/incoming/CHEESEHEAD/palm/realistic_runs/ches_IOP2/ensemble.member.7/01.ches_IOP02.12798/DATA_MASK_NETCDF_N03_M06slice
Saving: /air/lwanner/ches_IOP2/ensemble.member.7/01.ches_IOP02.12798/DATA_MASK_NETCDF_N03_M06slice_subsetLW
Storage needed :3158248
Reading: /bog/incoming/CHEESEHEAD/palm/realistic_runs/ches_IOP2/ensemble.member.7/01.ches_IOP02.12798/DATA_MASK_NETCDF_N03_M07slice
Saving: /air/lwanner/ches_IOP2/ensemble.member.7/01.ches_IOP02.12798/DATA_MA

In [ ]:
# stop